In [115]:
import pandas as pd
import datetime as dt
import numpy as np
from binance.client import Client
from binance.enums import HistoricalKlinesType

client = Client()
def get_historical_ohlc_data(symbol,past_days=None,interval=None):
    
    
    if not interval:
        interval='8h' # default interval 1 hour
    if not past_days:
        past_days=30  # default past days 30.

    start_str = '2023-01-01'
    end_str = '2024-01-01'
    #1y
    
    D=pd.DataFrame(client.get_historical_klines(symbol=symbol,start_str=start_str,end_str=end_str,interval=interval,klines_type=HistoricalKlinesType.SPOT))
    D.columns=['open_time','open', 'high', 'low', 'close', 'volume', 'close_time', 'qav', 'num_trades', 'taker_base_vol', 'taker_quote_vol','is_best_match']
    D['open_date_time']=[dt.datetime.fromtimestamp(x/1000) for x in D.open_time]
    D['symbol']=symbol
    D=D[['symbol','open_date_time','open', 'high', 'low', 'close']]#, 'volume', 'num_trades', 'taker_base_vol', 'taker_quote_vol']]

    return D


ConnectionError: HTTPSConnectionPool(host='api.binance.com', port=443): Max retries exceeded with url: /api/v3/ping (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x000001068AE96100>: Failed to establish a new connection: [Errno 11001] getaddrinfo failed'))

In [ ]:
RWA = ['BTCUSDT','ETHUSDT','BNBUSDT','SOLUSDT','XRPUSDT','ADAUSDT','AVAXUSDT','TRXUSDT','DOTUSDT','BCHUSDT']
#RWA = ['AVAXUSDT','ICPUSDT','MKRUSDT','SNXUSDT','RSRUSDT','CHRUSDT','DUSKUSDT']
#RWA = ['BNBUSDT','INJUSDT','GALAUSDT','CAKEUSDT','TWTUSDT','SFPUSDT','ONTUSDT']
ohlc_dic={}
for ticker in RWA:
    ohlc_dic[ticker] = get_historical_ohlc_data(symbol=ticker)

In [ ]:
import vectorbt as vbt
def custom_indicator(signal, entry_boundary, exit_boundary,short_entry_boundary, short_exit_boundary,short_sl, long_sl):#,long_out,short_out):
    long_res = np.where(signal <= entry_boundary,1,0)
    long_res = np.where(signal > exit_boundary,-1,long_res)
    long_res = np.where(signal < long_sl,0,long_res)
    #long_res = np.where(signal < long_out,-1,long_res) #s_score 停損停利
    short_res = np.where(signal >= short_entry_boundary,1,0)
    short_res = np.where(signal <= short_exit_boundary,-1,short_res)
    short_res = np.where(signal > short_sl,0,short_res)
    #short_res = np.where(signal > short_out,-1,short_res) #s_score 停損停利
    long_size = np.where(long_res==1,0.8,0)
    short_size = np.where(short_res==1,0.8,0)
    return long_res,short_res,long_size,short_size
MyInd = vbt.IndicatorFactory(
    class_name = 'ETF_arbitrage',
    short_name='ETF',
    input_names=['signal'],
    param_names=['entry', 'exit','short_entry', 'short_exit','short_sl','long_sl'],
    output_names=['long_res','short_res','long_size','short_size']
    ).from_apply_func(
        custom_indicator,
        keep_pd=True
        )

In [ ]:
def long_strat(signal, entry_boundary, exit_boundary, sl_boundary):
    long_res = np.where(signal <= entry_boundary,1,0)
    long_res = np.where(signal > exit_boundary,-1,long_res)
    #long_res = np.where(signal < long_out,-1,long_res)
    long_res = np.where(signal < sl_boundary,0,long_res)
    return long_res
long_ind = vbt.IndicatorFactory(
    class_name='long',
    short_name='lg',
    input_names=['signal'],
    param_names=['entry', 'exit','sl'],
    output_names=['long_res']
).from_apply_func(
    long_strat,
    keep_pd = True
)

def short_strat(signal, short_entry_boundary, short_exit_boundary, sl_boundary):
    short_res = np.where(signal >= short_entry_boundary,1,0)
    short_res = np.where(signal <= short_exit_boundary,-1,short_res)
    #short_res = np.where(signal > short_out,-1,short_res)
    short_res = np.where(signal > sl_boundary,0,short_res)
    return short_res
short_ind = vbt.IndicatorFactory(
    class_name='short',
    short_name='st',
    input_names=['signal'],
    param_names=['short_entry', 'short_exit','sl'],
    output_names=['short_res']
).from_apply_func(
    short_strat,
    keep_pd = True
)

In [ ]:
def process_trading_signals(signals):
    # Ensure input is a pandas Series
    if isinstance(signals, list):
        signals = pd.Series(signals)
    
    real_signals = np.zeros_like(signals)
    
    # Tracking state to determine if we are in a position
    in_position = False
    
    for i, signal in enumerate(signals):
        if signal == 1 and not in_position:
            real_signals[i] = 1
            in_position = True
        elif signal == -1 and in_position:
            real_signals[i] = -1
            in_position = False
    
    return pd.Series(real_signals)

In [ ]:
import numpy as np
from scipy import linalg
from sklearn.linear_model import LinearRegression
from statsmodels.tsa.ar_model import AutoReg
import plotly.express as px
import quantstats as qs
qs.extend_pandas()
time_len = ohlc_dic[RWA[0]]['close'].size
predict_s_score_list = []
total_return = pd.DataFrame()
total_holding = pd.DataFrame()
opt_entry_list = []
opt_short_entry_list = []
opt_exit_list = []
opt_short_exit_list = []
time_index = []
for l in range(180,time_len,30):
    train_return_df = pd.DataFrame()
    train_close_df = pd.DataFrame()
    test_return_df = pd.DataFrame()
    test_close_df = pd.DataFrame()
    train_ohlc_dic = {}
    test_ohlc_dic = {}
    #RWA = ['BTCUSDT','ETHUSDT','BNBUSDT','SOLUSDT','XRPUSDT','ADAUSDT','AVAXUSDT','TRXUSDT','DOTUSDT','BCHUSDT']
    #RWA = ['BNBUSDT','INJUSDT','GALAUSDT','CAKEUSDT','TWTUSDT','SFPUSDT','ONTUSDT']
    for ticker in RWA:
        train_ohlc_dic[ticker] = ohlc_dic[ticker].iloc[l-180:l-30,:]
        test_ohlc_dic[ticker] = ohlc_dic[ticker].iloc[l-180:l,:]

        train_ohlc_dic[ticker]['open'] = train_ohlc_dic[ticker]['open'].astype(float)
        train_ohlc_dic[ticker]['close'] = train_ohlc_dic[ticker]['close'].astype(float)
        train_ohlc_dic[ticker]['return'] = train_ohlc_dic[ticker]['close']/train_ohlc_dic[ticker]['open'] - 1
        train_return_df[ticker] = train_ohlc_dic[ticker]['return']
        train_close_df[ticker] = train_ohlc_dic[ticker]['close']

        test_ohlc_dic[ticker]['open'] = test_ohlc_dic[ticker]['open'].astype(float)
        test_ohlc_dic[ticker]['close'] = test_ohlc_dic[ticker]['close'].astype(float)
        test_ohlc_dic[ticker]['return'] = test_ohlc_dic[ticker]['close']/test_ohlc_dic[ticker]['open'] - 1
        test_return_df[ticker] = test_ohlc_dic[ticker]['return']
        test_close_df[ticker] = test_ohlc_dic[ticker]['close']
    
    std_df = (train_return_df - train_return_df.mean() ) / train_return_df.std()
    cov_matrix = std_df.cov()
    '''
    #btc_covariances = cov_matrix['BTCUSDT']
    #top_5_cryptos = btc_covariances.abs().sort_values(ascending=False).index[1:5]

    # Create a new covariance matrix for BTC and the top 5 cryptocurrencies
    #selected_cryptos = ['BTCUSDT'] + list(top_5_cryptos)
    selected_crypto = cov_matrix[cov_matrix['BTCUSDT'] > 0.7].index
    if len(selected_crypto) > 3:
        new_cov_matrix = cov_matrix.loc[selected_crypto, selected_crypto]
    else:
        continue
    cov_matrix = new_cov_matrix
    RWA = selected_crypto
    train_return_df = pd.DataFrame()
    train_close_df = pd.DataFrame()
    test_return_df = pd.DataFrame()
    test_close_df = pd.DataFrame()
    train_ohlc_dic = {}
    test_ohlc_dic = {}
    for ticker in RWA:
        train_ohlc_dic[ticker] = ohlc_dic[ticker].iloc[l-180:l-30,:]
        test_ohlc_dic[ticker] = ohlc_dic[ticker].iloc[l-30:l,:]

        train_ohlc_dic[ticker]['open'] = train_ohlc_dic[ticker]['open'].astype(float)
        train_ohlc_dic[ticker]['close'] = train_ohlc_dic[ticker]['close'].astype(float)
        train_ohlc_dic[ticker]['return'] = train_ohlc_dic[ticker]['close']/train_ohlc_dic[ticker]['open'] - 1
        train_return_df[ticker] = train_ohlc_dic[ticker]['return']
        train_close_df[ticker] = train_ohlc_dic[ticker]['close']

        test_ohlc_dic[ticker]['open'] = test_ohlc_dic[ticker]['open'].astype(float)
        test_ohlc_dic[ticker]['close'] = test_ohlc_dic[ticker]['close'].astype(float)
        test_ohlc_dic[ticker]['return'] = test_ohlc_dic[ticker]['close']/test_ohlc_dic[ticker]['open'] - 1
        test_return_df[ticker] = test_ohlc_dic[ticker]['return']
        test_close_df[ticker] = test_ohlc_dic[ticker]['close']
    '''
    eigenValues, eigenVectors = np.linalg.eig(cov_matrix)
    idx = eigenValues.argsort()[::-1]
    eigenValues = eigenValues[idx]
    eigenVectors = eigenVectors[:,idx]
    eigenVectors = eigenVectors.T
    eigenVectors[0] = eigenVectors[0]*-1
    explainVarRatio = eigenValues / sum(eigenValues)
    total_explain_var = 0
    threshhold = 0.8
    num = 0
    for explain_variance in explainVarRatio:
        if total_explain_var < threshhold:
            total_explain_var = total_explain_var + explain_variance
            num = num + 1

    std = np.std(train_return_df, axis=0)

    weight = []
    for j in range(num):
        a = []
        for k in range(len(RWA)):
            a.append(eigenVectors[j][k]/std[k])
        a = a / sum(np.abs(a))
        weight.append(a)
    weight = np.array(weight)
    if (weight < 0).all():
        weight = weight * -1
    ETF = pd.DataFrame()
    test_ETF = pd.DataFrame()
    ETF_cum = pd.DataFrame()
    test_ETF_cum = pd.DataFrame()
    for j in range(num):
        ETF[j] = train_return_df.dot(weight[j])
        test_ETF[j] = test_return_df.dot(weight[j])
        ETF_cum[j] = (1+ETF[j]).cumprod()
    residual= pd.DataFrame()
    test_residual = pd.DataFrame()
    for symbol in RWA:
        y = train_return_df[symbol]
        X = ETF
        X_star = test_ETF
        model = LinearRegression()
        model.fit(X, y)
        y_pred = model.predict(X)
        residual[symbol] = train_return_df[symbol] - y_pred
        test_y_pred = model.predict(X_star)
        test_residual[symbol] = test_return_df[symbol] - test_y_pred
        a = test_y_pred - model.intercept_
        test_ETF_cum[symbol] = (1+a).cumprod()
    residuals = residual.cumsum()
    residuals.iloc[-1] = 0
    residuals = residuals.reset_index()
    params_list = []
    variance_list = []
    for symbol in RWA:
        model = AutoReg(residuals[symbol], lags=1).fit()
        params = pd.DataFrame({'const': model.params.iloc[0], 'L1': model.params.iloc[1]}, index=[symbol])
        params_list.append(params)
        variance_list.append(np.std(model.resid))

    params_df = pd.concat(params_list)
    variance = pd.DataFrame(data=variance_list).T
    variance.columns = RWA

    ar_params , sigma_square = params_df.T, variance
    kappa = pd.DataFrame(-np.log(ar_params.iloc[1])*365*3).T
    m = pd.DataFrame(residual.mean()).T
    sd_OU = pd.DataFrame(np.sqrt(sigma_square.iloc[0]/ (2*kappa.iloc[0]))).T
    param = pd.concat([kappa, m, sd_OU])
    param.index = ['kappa', 'm', 'sd_OU']
    train_s_score = (residual - param.loc['m']) / param.loc['sd_OU']
    s_score = (test_residual - param.loc['m']) / param.loc['sd_OU']
    train_signal = train_s_score 
    signal = s_score
    all_values = train_signal.values.flatten()
    entry_range = np.percentile(all_values, np.arange(5,100,5))
    period_return = pd.DataFrame()
    period_holding = pd.DataFrame()

    #entry_list = np.arange(entry_range[0],entry_range[1],0.1)
    #short_entry_list = np.arange(entry_range[17],entry_range[18],0.1)
    entry_list = np.arange(-2,-1.5,0.1)
    short_entry_list = np.arange(1.5,2,0.1)
    best_sharpe = -999
    opt_entry = 0
    opt_exit = 0
    opt_short_entry = 0
    opt_short_exit = 0
    for ent in entry_list:
        for ex in np.arange(ent+0.3,ent+0.8,0.1):
                res = long_ind.run(train_signal,entry=ent,exit=ex,sl=-2.5)
                entry = res.long_res == 1
                exit = res.long_res == -1
                strat_return = pd.DataFrame()
                pf_1 = vbt.Portfolio.from_signals(train_close_df,entries=entry,exits=exit,freq='8h',fees=0.00036,slippage=0.0005,sl_stop=0.1)
                a= pf_1.returns()/len(RWA)
                a_sum = a.sum(axis=1)
                sharpe = a_sum.sharpe()
                count = pf_1.trades.count().sum()
                sharpe = sharpe*np.sqrt(count)
                if sharpe >= best_sharpe:
                    best_sharpe = sharpe
                    opt_entry = ent
                    opt_exit = ex
    #if best_sharpe < 0:
    #    opt_entry = -999
    best_sharpe = -999
    for short_ent in short_entry_list:
        for short_ex in np.arange(short_ent-0.8,short_ent-0.3,0.1):
            res = short_ind.run(train_signal,short_entry=short_ent,short_exit=short_ex,sl=2.5)#,short_out=entry_range[18])#
            short_entry = res.short_res == 1
            short_exit = res.short_res == -1
            pf_2 = vbt.Portfolio.from_signals(train_close_df,short_entries=short_entry,short_exits=short_exit,freq='8h',fees=0.00036,slippage=0.0005,sl_stop=0.1)
            b = pf_2.returns()/len(RWA)
            b_sum = b.sum(axis=1)
            sharpe = b_sum.sharpe()
            count = pf_2.trades.count().sum()
            sharpe = sharpe*np.sqrt(count)
            if sharpe >= best_sharpe:
                    best_sharpe = sharpe
                    opt_short_entry = short_ent
                    opt_short_exit = short_ex
    #if best_sharpe:
    #    opt_short_entry = 999
    #print(opt_entry)
    #print(opt_exit)
    temp = pd.DataFrame()
    for symbol in RWA:
        res = MyInd.run(signal[symbol],entry=opt_entry,exit=opt_exit,short_entry=opt_short_entry,short_exit=opt_short_exit,short_sl=2.5
                        ,long_sl=-2.5)
        entry = res.long_res == 1
        exit = res.long_res == -1
        if entry.iloc[-1] == True:
            entry.iloc[-1] = False
        short_entry = res.short_res == 1
        short_exit = res.short_res == -1
        if short_entry.iloc[-1] == True:
            short_entry.iloc[-1] = False
        entry_int_list = [int(value) for value in entry]
        exit_indices = np.where(exit)[0]
        for index in exit_indices:
            if index < len(entry_int_list):
                entry_int_list[index] = -1
        entry_int_list = process_trading_signals(entry_int_list)
        start_indices = [i for i, x in enumerate(entry_int_list) if x == 1]
        end_indices = [i for i, x in enumerate(entry_int_list) if x == -1]
        pairs = []
        for start in start_indices:
            for end in end_indices:
                if end > start:
                    pairs.append((start, end))
                    break
        for start, end in pairs:
            for i in range(start, end + 1):
                entry_int_list[i] = 1
        short_entry_int_list = [int(value) for value in short_entry]
        short_exit_indices = np.where(short_exit)[0]
        for index in short_exit_indices:
            if index < len(short_entry_int_list):
                short_entry_int_list[index] = -1
        short_entry_int_list = process_trading_signals(short_entry_int_list)
        start_indices = [a for a, x in enumerate(short_entry_int_list) if x == 1]
        end_indices = [b for b, y in enumerate(short_entry_int_list) if y == -1]
        pairs = []
        for start in start_indices:
            for end in end_indices:
                if end > start:
                    pairs.append((start, end))
                    break
        for start, end in pairs:
            for i in range(start, end + 1):
                short_entry_int_list[i] = -1
        temp[symbol] = np.array(entry_int_list) + np.array(short_entry_int_list)
        pf_1 = vbt.Portfolio.from_signals(test_close_df[symbol],entries=entry,exits=exit,freq='8h',fees=0.00036,slippage=0.0005,sl_stop=0.1)#,size=res.long_size,size_type='percent',
        pf_2 = vbt.Portfolio.from_signals(test_close_df[symbol],short_entries=short_entry,short_exits=short_exit,freq='8h',fees=0.00036,slippage=0.0005,sl_stop=0.1)#,size=res.short_size,size_type='percent',
        period_return[symbol] = pf_1.returns() + pf_2.returns()
    opt_entry_list.append(opt_entry)
    opt_exit_list.append(opt_exit)
    opt_short_entry_list.append(opt_short_entry)
    opt_short_exit_list.append(opt_short_exit)
    time_index.append(test_ohlc_dic[RWA[0]]['open_date_time'][l-30])
    temp = temp.set_index(test_ohlc_dic[RWA[0]]['open_date_time'])
    total_holding = pd.concat([total_holding, temp],ignore_index=False)
    period_return = period_return.set_index(test_ohlc_dic[RWA[0]]['open_date_time'])
    total_return = pd.concat([total_return, period_return],ignore_index=False)

C:\Users\xiuhu\AppData\Local\Temp\ipykernel_3920\4056668466.py:30: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\xiuhu\AppData\Local\Temp\ipykernel_3920\4056668466.py:31: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\xiuhu\AppData\Local\Temp\ipykernel_3920\4056668466.py:32: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/panda

In [ ]:
total_return

BTCUSDT  ETHUSDT  BNBUSDT  SOLUSDT   XRPUSDT  ADAUSDT  \
open_date_time                                                               
2022-01-01 08:00:00      0.0      0.0      0.0      0.0  0.000000      0.0   
2022-01-01 16:00:00      0.0      0.0      0.0      0.0  0.000000      0.0   
2022-01-02 00:00:00      0.0      0.0      0.0      0.0  0.000000      0.0   
2022-01-02 08:00:00      0.0      0.0      0.0      0.0  0.000000      0.0   
2022-01-02 16:00:00      0.0      0.0      0.0      0.0  0.000000      0.0   
...                      ...      ...      ...      ...       ...      ...   
2023-12-30 16:00:00      0.0      0.0      0.0      0.0  0.008777      0.0   
2023-12-31 00:00:00      0.0      0.0      0.0      0.0  0.000000      0.0   
2023-12-31 08:00:00      0.0      0.0      0.0      0.0  0.000000      0.0   
2023-12-31 16:00:00      0.0      0.0      0.0      0.0  0.000000      0.0   
2024-01-01 00:00:00      0.0      0.0      0.0      0.0  0.000000      0.0   

                     AVAXUSDT   TRXUSDT  DOTUSDT   BCHUSDT  
open_date_time                                              
2022-01-01 08:00:00       0.0  0.000000      0.0  0.000000  
2022-01-01 16:00:00       0.0  0.000000      0.0  0.000000  
2022-01-02 00:00:00       0.0 -0.000859      0.0  0.000000  
2022-01-02 08:00:00       0.0 -0.004642      0.0  0.000000  
2022-01-02 16:00:00       0.0  0.000000      0.0  0.000000  
...                       ...       ...      ...       ...  
2023-12-30 16:00:00       0.0  0.000000      0.0  0.000000  
2023-12-31 00:00:00       0.0  0.000000      0.0 -0.000859  
2023-12-31 08:00:00       0.0  0.000000      0.0 -0.010351  
2023-12-31 16:00:00       0.0  0.000000      0.0 -0.016162  
2024-01-01 00:00:00       0.0  0.000000      0.0  0.000000  

[12240 rows x 10 columns]

In [ ]:
import plotly.graph_objects as go

fig = go.Figure()
time_index
# Add scatter plot for each type of action
fig.add_trace(go.Scatter(x=opt_entry_list, y=time_index, mode='markers', name='Entry', marker=dict(color='blue')))
fig.add_trace(go.Scatter(x=opt_exit_list, y=time_index, mode='markers', name='Exit', marker=dict(color='green')))
fig.add_trace(go.Scatter(x=opt_short_entry_list, y=time_index, mode='markers', name='Short Entry', marker=dict(color='red')))
fig.add_trace(go.Scatter(x=opt_short_exit_list, y=time_index, mode='markers', name='Short Exit', marker=dict(color='purple')))

# Set plot layout
fig.update_layout(
    title='All Optimal Signal',
    xaxis_title='Value',
    yaxis_title='Period Index',
    legend_title='Action Type'
)

# Show the plot
fig.show()

In [ ]:
total_holding_sum = total_holding.sum(axis=1)
fig = px.line(total_holding_sum)
fig.show()

c:\Users\xiuhu\AppData\Local\Programs\Python\Python39\lib\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result



In [ ]:
re = total_return/len(RWA)
re_sum = re.sum(axis=1)
import quantstats as qs
qs.extend_pandas()
qs.reports.full(re_sum,compounded=True,periods_per_year=365)

KeyError: "Cannot get right slice bound for non-unique label: Timestamp('2022-01-23 00:00:00')"